Prueba_Dani


In [1]:
# Paquetes del notebook visto en clase
import nltk
nltk.download('wordnet')
from nltk.corpus import wordnet as wn

# Cargamos otros paquetes que nos pueden ser útiles
import pandas as pd

[nltk_data] Downloading package wordnet to C:\Users\Daniel
[nltk_data]     Parra\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!



# Paso 1
Hay que cargar el archivo `NRC-EmoLex.txt` y decidir cómo organizarlo para que tenga un acceso rápido en memoria. (Este archivo lo obtivimos borrando la última columna que se correspondía a su traducción al español).


In [ ]:
Tabla_emo=pd.read_csv('NRC-EmoLex.txt', sep='\t')
print(Tabla_emo.head())

## Podríamos eliminar las filas que sumen 0 para que "sea una búsqueda más rápida"


  English Word  anger  anticipation  disgust  fear  joy  negative  positive  \
0        aback      0             0        0     0    0         0         0   
1       abacus      0             0        0     0    0         0         0   
2      abandon      0             0        0     1    0         1         0   
3    abandoned      1             0        0     1    0         1         0   
4  abandonment      1             0        0     1    0         1         0   

   sadness  surprise  trust  
0        0         0      0  
1        0         0      1  
2        1         0      0  
3        1         0      0  
4        1         1      0  


In [ ]:
print(Tabla_emo.iloc[:, 0])
print(Tabla_emo.iloc[:, 0]=='aback')
print(Tabla_emo[Tabla_emo.iloc[:, 0]=='aback'])
prueba=Tabla_emo[Tabla_emo.iloc[:, 0]=='abandon']
print(prueba.columns[(prueba==1).any()]) ## Para saber el tipo de emoción

#print(Tabla_emo[Tabla_emo.iloc[:, 0]=='abandon', Tabla_emo.iloc[Tabla_emo.iloc[:, 0]=='abandon', 1:]==1])

0              aback
1             abacus
2            abandon
3          abandoned
4        abandonment
            ...     
14149           zone
14150            zoo
14151     zoological
14152        zoology
14153           zoom
Name: English Word, Length: 14154, dtype: object
0         True
1        False
2        False
3        False
4        False
         ...  
14149    False
14150    False
14151    False
14152    False
14153    False
Name: English Word, Length: 14154, dtype: bool
  English Word  anger  anticipation  disgust  fear  joy  negative  positive  \
0        aback      0             0        0     0    0         0         0   

   sadness  surprise  trust  
0        0         0      0  
Index(['fear', 'negative', 'sadness'], dtype='object')


Ahora preparamos una función capaz de identificar la emoción

In [ ]:
def get_emo(palabra):
    Emo=
    fila=Tabla_emo[Tabla_emo.iloc[:, 0]==palabra]
    print(fila)
    if sum(Tabla_emo.iloc[:, 1:])==0:
        print("No hay una emoción con la que se corresponda")

Emo=get_emo('aback')
print(Emo)

  English Word  anger  anticipation  disgust  fear  joy  negative  positive  \
0        aback      0             0        0     0    0         0         0   

   sadness  surprise  trust  
0        0         0      0  


# Paso 2
Utilizar WordNet desde NLTK paraincluir sinónimos, hipónimos, hiperónimos y palabras derivadas en la tabla.

# Aquí ponemos chunks antiguos que hice en el trabajo y sen van a borrar (por si resultan importantes por X motivo)

In [ ]:
## BORRAR

# Extendemos el léxico NRC usando relaciones de WordNet y el diccionario generado en el apartado 1: Diccionario {palabra: [emociones]}.

# Para cada palabra en el léxico original:
# - Obtiene sinónimos (synsets)
# - Obtiene hipónimos (términos más específicos)
# - Obtiene hiperónimos (términos más generales)
# - Obtiene formas derivadas (como plurales)
# Finalmente obtendremos un diccionario {(lemma, pos_tag): [emociones]} con dichas implementaciones


# Función útil para guardar correctamente en el diccionario extendido.
def add_to_lexicon(key, emotions):
    """
    Añade la key y las emociones al diccionario extendido asegurándose de que no se reescriban las keys y acumulando las emociones (sin que se dupliquen) 
    en caso de que haya repeticiones.
    
    Args:
        key: tupla construida con el lemma y el POS-tag de la palabra.
        emotions: emociones correspondientes a la key proporcionada.
    
    Returns:
        dict: Diccionario actualizado {(lemma, POS-tag): [lista_de_emociones]} expandido y sin repeticiones
    """
    if key in extended_lexicon:
        # Para combinar sin duplicar y no arriesgarnos a perder información
        extended_lexicon[key] = list(set(extended_lexicon[key]) | set(emotions))
    else:
        extended_lexicon[key] = emotions


# Código para expandir el díccionario
extended_lexicon = {}

print("Extendiendo léxico con WordNet...")

for word, emotions in nrc_lexicon.items():
    # Obtenemos synsets de la palabra
    synsets = wn.synsets(word)
    
    for synset in synsets:
        # POS tag de WordNet y buscamos su complementario en penn
        wn_pos = synset.pos()
        penn_pos = wordnet_to_penn.get(wn_pos, 'NN')    # Le indicamos que, en caso de no encontrar su correspondiente en el diccionario utilice 'NN'
        
        # Agregamos la palabra original, la cual de por sí es lemma
        key = (word, penn_pos)    
        add_to_lexicon(key, emotions)
        
        # Agregamos los sinónimos del synset
        for lemma in synset.lemmas():
            lemma_name = lemma.name().replace('_', ' ').lower()
            key = (lemma_name, penn_pos)
            add_to_lexicon(key, emotions)
            
            
            # Agregamos formas derivadas
            try:
                for related in lemma.derivationally_related_forms():
                    related_pos = related.synset().pos()
                    related_penn = wordnet_to_penn.get(related_pos, 'NN')
                    related_name = related.name().replace('_', ' ').lower()
                    key = (related_name, related_penn)
                    add_to_lexicon(key, emotions)
            except:
                pass
        
        # Agregamos los hipónimos (términos más específicos)
        for hyponym in synset.hyponyms():
            for lemma in hyponym.lemmas():
                hyp_name = lemma.name().replace('_', ' ').lower()
                hyp_pos = wordnet_to_penn.get(hyponym.pos(), 'NN')
                key = (hyp_name, hyp_pos)
                add_to_lexicon(key, emotions)
        
        # Agragamos los hiperónimos (términos más generales)
        for hypernym in synset.hypernyms():
            for lemma in hypernym.lemmas():
                hyper_name = lemma.name().replace('_', ' ').lower()
                hyper_pos = wordnet_to_penn.get(hypernym.pos(), 'NN')
                key = (hyper_name, hyper_pos)
                add_to_lexicon(key, emotions)

# Nos aseguramos de que no haya duplicados y de que estén ordenados
for k in extended_lexicon:
    extended_lexicon[k] = sorted(set(extended_lexicon[k]))

print(f"Léxico extendido de {len(nrc_lexicon)} a {len(extended_lexicon)} entradas")


#####################################################################################
# Código para generar el diccionario con el léxicon no expandido:
original_lexicon = {}

print("\nObteniendo diccionario de léxico no extendido con WordNet...")

for word, emotions in nrc_lexicon.items():
    # Obtener synsets de la palabra
    synsets = wn.synsets(word)
    
    for synset in synsets:
        # POS tag de WordNet y buscamos su complementario en penn
        wn_pos = synset.pos()
        penn_pos = wordnet_to_penn.get(wn_pos, 'NN')    # Le indicamos que, en caso de no encontrar su correspondiente en el diccionario utilice 'NN'
        
        # Agregamos la palabra original, la cual de por sí es lemma
        key = (word, penn_pos)    
        original_lexicon[key] = emotions

# Nos aseguramos de que no haya duplicados y de que estén ordenados
for k in original_lexicon:
    original_lexicon[k] = sorted(set(original_lexicon[k]))

print(f"Son iguales las entradas originales: {len(nrc_lexicon)} a las de lexicón no extendido: {len(original_lexicon)} entradas")


Extendiendo léxico con WordNet...
Léxico extendido de 6453 a 55155 entradas

Obteniendo diccionario de léxico no extendido con WordNet...
Son iguales las entradas originales: 6453 a las de lexicón no extendido: 9469 entradas


In [ ]:
## BORRAR
# Mostrar ejemplos 
print("\nEjemplos del léxico extendido:")
for key in list(extended_lexicon.keys())[:10]:
    print(f"  {key}: {extended_lexicon[key]}")


Ejemplos del léxico extendido:
  ('abacus', 'NN'): ['positive', 'trust']
  ('tablet', 'NN'): ['positive', 'trust']
  ('calculator', 'NN'): ['anger', 'disgust', 'fear', 'negative', 'positive', 'sadness', 'trust']
  ('calculating machine', 'NN'): ['anger', 'disgust', 'fear', 'negative', 'positive', 'sadness', 'trust']
  ('abandon', 'NN'): ['anticipation', 'fear', 'joy', 'negative', 'positive', 'sadness', 'trust']
  ('wantonness', 'NN'): ['anger', 'disgust', 'fear', 'negative', 'sadness']
  ('wanton', 'JJS'): ['fear', 'negative', 'sadness']
  ('unconstraint', 'NN'): ['fear', 'negative', 'sadness']
  ('unrestraint', 'NN'): ['fear', 'negative', 'sadness']
  ('wildness', 'NN'): ['anger', 'anticipation', 'disgust', 'fear', 'joy', 'negative', 'positive', 'sadness', 'surprise', 'trust']


In [ ]:
## BORRAR
## Resultados Dania

In [ ]:
## BORRAR
# Realizamos el análisis
analysis_results = analyze_all_books(book_texts, extended_lexicon)

Analizando emociones en las novelas...

Analizando: Crime and Punishment...  POS desconocido 'c' para palabra 'and'. Se omite.
 POS desconocido 'c' para palabra 'by'. Se omite.
 POS desconocido 'c' para palabra 'by'. Se omite.
 POS desconocido 'c' para palabra 'a'. Se omite.
 POS desconocido 'c' para palabra 'about'. Se omite.
 POS desconocido 'c' para palabra 'the'. Se omite.
 POS desconocido 'c' para palabra 'to'. Se omite.
 POS desconocido 'c' para palabra 'the'. Se omite.
 POS desconocido 'c' para palabra 'of'. Se omite.
 POS desconocido 'c' para palabra 'a'. Se omite.
 POS desconocido 'c' para palabra 'and'. Se omite.
 POS desconocido 'c' para palabra 'but'. Se omite.
 POS desconocido 'c' para palabra 'that'. Se omite.
 POS desconocido 'c' para palabra 'with'. Se omite.
 POS desconocido 'c' para palabra 'five'. Se omite.
 POS desconocido 'c' para palabra 'in'. Se omite.
 POS desconocido 'c' para palabra 'two'. Se omite.
 POS desconocido 'c' para palabra 'the'. Se omite.
 POS desco

# Versión léxico NO extendido
## Tarea 4: Analizar emociones en los textos (3.0 puntos)

In [ ]:
# Realizamos el análisis para el léxico no extendido
analysis_results = analyze_all_books(book_texts, original_lexicon)

Analizando emociones en las novelas...

Analizando: Crime and Punishment...  POS desconocido 'c' para palabra 'and'. Se omite.
 POS desconocido 'c' para palabra 'by'. Se omite.
 POS desconocido 'c' para palabra 'by'. Se omite.
 POS desconocido 'c' para palabra 'a'. Se omite.
 POS desconocido 'c' para palabra 'about'. Se omite.
 POS desconocido 'c' para palabra 'the'. Se omite.
 POS desconocido 'c' para palabra 'to'. Se omite.
 POS desconocido 'c' para palabra 'the'. Se omite.
 POS desconocido 'c' para palabra 'of'. Se omite.
 POS desconocido 'c' para palabra 'a'. Se omite.
 POS desconocido 'c' para palabra 'and'. Se omite.
 POS desconocido 'c' para palabra 'but'. Se omite.
 POS desconocido 'c' para palabra 'that'. Se omite.
 POS desconocido 'c' para palabra 'with'. Se omite.
 POS desconocido 'c' para palabra 'five'. Se omite.
 POS desconocido 'c' para palabra 'in'. Se omite.
 POS desconocido 'c' para palabra 'two'. Se omite.
 POS desconocido 'c' para palabra 'the'. Se omite.
 POS desco

#### Conclusiones

En esta sección, comenta brevemente los resultados obtenidos.
* ¿Qué emociones son las más frecuentes en general?
* ¿Hay novelas que destacan por alguna emoción en particular?
* ¿Qué limitaciones has encontrado?